In [4]:
import pandas as pd
import numpy as np
import matplotlib as plt
#import seaborn as sns
from datetime import datetime
#import scipy.stats as stats
#import statsmodels.api as sm
import re
from shapely.geometry import Point
import geopandas as gpd
#import folium
#from folium.plugins import MarkerCluster
#from folium.plugins import FastMarkerCluster
from ipywidgets import interact, interactive, fixed, interact_manual
import plotly.express as px
import plotly.graph_objects as go
from plotly.colors import n_colors
import chart_studio
import chart_studio.plotly as py
import plotly.figure_factory as ff

pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 100)
pd.set_option('display.width', 1000)

## Load in AirBNB dataset with gentrifying classifier

In [5]:
airbnb_final = pd.read_csv('../data/airbnb_gentrification.csv')

In [6]:
airbnb_final.head()

Unnamed: 0  listing_id                              comments_concatenated                                            name  host_id  latitude  longitude  price  minimum_nights  number_of_reviews  reviews_per_month  calculated_host_listings_count  availability_365                          listing_url                                        description                              neighborhood_overview  host_since  host_listings_count          property_type  accommodates  bathrooms_text  bedrooms  beds                                          amenities  minimum_nights_avg_ntm  maximum_nights_avg_ntm  review_scores_rating  review_scores_accuracy  review_scores_cleanliness  review_scores_checkin  review_scores_communication  review_scores_location  review_scores_value  zip_code         GEOID  house_price_2021-01-31  house_pct_change  rentals_2021-01-31  rental_price_pct_change  new_restaurants  available_beer  str_permits_2020  str_permits_growth  crimes  total_pop_2010  total_pop_2019  \
0           0        6422  I can't say enough about how wonderful it was ...                                 Nashville Charm    12172  36.17315  -86.73581     40              30                674               4.69                               1               267    https://www.airbnb.com/rooms/6422  30 day or more rental during COVID. Show COVID...  Historic East Nashville is home to many new an...  2009-04-03                  0.0  Private room in house             2  1 private bath       2.0   3.0  ["Hair dryer", "Bathtub", "Lock on bedroom doo...                    30.0                   365.0                  99.0                    10.0                       10.0                   10.0                         10.0                    10.0                 10.0   37206.0  4.703701e+10                412476.0             38.31                 NaN                      NaN              1.0             2.0             114.0               114.0  1165.0          2544.0          2100.0   
1           1       25613  Nell and Michael made my stay pleasant and eas...  Room in Historic East Nashville Craftsman Home    95811  36.17826  -86.74162     75               2                510               3.87                               1                63   https://www.airbnb.com/rooms/25613  Serve up some sweet sounds on the piano and wi...  This home is in a walkable neighborhood with i...  2010-03-18                  1.0  Private room in house             2  1 private bath       1.0   1.0  ["Hair dryer", "Carbon monoxide alarm", "Air c...                     2.0                  1125.0                  97.0                    10.0                       10.0                   10.0                         10.0                    10.0                 10.0   37206.0  4.703701e+10                412476.0             38.31                 NaN                      NaN              3.0            12.0             101.0               101.0  1048.0          2485.0          2525.0   
2           2      136015  Very relaxing, beautiful property, and warm / ...               Apart. on the Ridge near Opryland   666322  36.19464  -86.67195    103              30                 50               0.43                               2               190  https://www.airbnb.com/rooms/136015  Fantastic View! Overlooks farms and is on the ...              Dead end street with great neighbors!  2011-06-05                  4.0       Entire apartment             2          1 bath       1.0   1.0  ["Fire extinguisher", "Wifi", "Dryer", "Washer...                    30.0                  1125.0                  97.0                    10.0                       10.0                   10.0                         10.0                    10.0                 10.0   37214.0  4.703702e+10                278031.0             65.43              1581.0                    22.18              9.0           112.0              48.0                48.0  4429.0          5411.0          6024.0   

In [162]:
airbnb_final.groupby('gentrifying')['review_scores_communication'].mean()

gentrifying
False    9.839259
True     9.889302
Name: review_scores_communication, dtype: float64

In [7]:
#About 21% of AirBNBs are in gentrifying neighborhoods
airbnb_final.groupby('gentrifying').count()['listing_id']

gentrifying
False    4107
True     1098
Name: listing_id, dtype: int64

In [9]:
#About 8% of population lives in gentrifying neighborhoods
airbnb_final.drop_duplicates('GEOID').groupby('gentrifying').sum()['total_pop_2019']

gentrifying
False    602426.0
True      52293.0
Name: total_pop_2019, dtype: float64

In [166]:
airbnb_medians = airbnb_final.drop_duplicates('GEOID')
airbnb_medians = airbnb_medians.groupby('gentrifying').median().reset_index()
airbnb_medians

gentrifying  Unnamed: 0  listing_id     host_id   latitude  longitude  price  minimum_nights  number_of_reviews  reviews_per_month  calculated_host_listings_count  availability_365  host_listings_count  accommodates  bedrooms  beds  minimum_nights_avg_ntm  maximum_nights_avg_ntm  review_scores_rating  review_scores_accuracy  review_scores_cleanliness  review_scores_checkin  review_scores_communication  review_scores_location  review_scores_value  zip_code         GEOID  house_price_2021-01-31  house_pct_change  rentals_2021-01-31  rental_price_pct_change  new_restaurants  available_beer  str_permits_2020  str_permits_growth  crimes  total_pop_2010  total_pop_2019  total_pop_change  total_pop_pct_change  pop_over25_2010  pop_over25_2019  pop_over25_change  pop_over25_pcg_change  total_households_2010  total_households_2019  total_households_change  total_households_pct_change  white_pct_2010  white_pct_2019  white_value_change  white_pct_change  bach_pct_2010  bach_pct_2019  \
0        False       378.5   7800369.5  30442462.0  36.134915  -86.73512   98.5             2.0               84.5               1.61                             1.0             180.0                  1.0           4.0       2.0   2.0                     2.0                  1125.0                  98.0                    10.0                       10.0                   10.0                         10.0                    10.0                 10.0   37209.0  4.703702e+10                304542.0             51.35              1634.0                   18.350              3.0             4.0               9.0                 9.0  1958.0          4013.0          4313.0             383.0              0.100704           2616.0           2978.0              296.0               0.119845                 1626.0                 1752.0                     82.0                     0.050708        0.670178        0.683127           -0.014736         -0.017303       0.294748       0.360305   
1         True       104.0   3464176.0  10259524.0  36.172300  -86.76923   94.0             2.0              115.0               2.06                             2.0             199.0                  3.0           6.0       3.0   3.0                     2.0                  1125.0                  97.0                    10.0                       10.0                   10.0                         10.0                    10.0                 10.0   37208.0  4.703701e+10                351685.0             71.28              1587.0                   26.035              4.0             6.0              68.0                68.0  3457.0          3114.0          3330.0             125.0              0.039002           2224.0           2355.0              223.0               0.161502                 1218.0                 1187.0                    149.0                     0.144168        0.329077        0.547935            0.154414          0.573470       0.101292       0.325690   

   bach_value_change  bach_pct_change  rent_pct_2010  rent_pct_2019  rent_value_change  renter_pct_change  median_hhi_2010  median_hhi_2019  median_hhi_value_change  median_hhi_pct_change  poverty_pct_2010  poverty_pct_2019  poverty_value_change  poverty_pct_change  
0           0.052757         0.136121       0.409055       0.438809           0.040835           0.097123          44566.0          58961.0                  12960.5               0.278539              10.6             12.75                   2.7            0.391304  
1           0.208381         1.608310       0.496795       0.476832          -0.019022          -0.049551          24026.0          50764.0                  25150.0               0.954608              26.2             18.90                  -8.8           -0.335878

In [168]:
airbnb_means = airbnb_final.copy()
airbnb_means = airbnb_means.groupby('gentrifying').mean().reset_index()
airbnb_means

gentrifying   Unnamed: 0    listing_id       host_id   latitude  longitude       price  minimum_nights  number_of_reviews  reviews_per_month  calculated_host_listings_count  availability_365  host_listings_count  accommodates  bedrooms      beds  minimum_nights_avg_ntm  maximum_nights_avg_ntm  review_scores_rating  review_scores_accuracy  review_scores_cleanliness  review_scores_checkin  review_scores_communication  review_scores_location  review_scores_value      zip_code         GEOID  house_price_2021-01-31  house_pct_change  rentals_2021-01-31  rental_price_pct_change  new_restaurants  available_beer  str_permits_2020  str_permits_growth       crimes  total_pop_2010  total_pop_2019  total_pop_change  total_pop_pct_change  pop_over25_2010  pop_over25_2019  pop_over25_change  pop_over25_pcg_change  total_households_2010  total_households_2019  total_households_change  total_households_pct_change  white_pct_2010  white_pct_2019  white_value_change  white_pct_change  \
0        False  2643.350621  2.952264e+07  1.108377e+08  36.155991 -86.768615  214.973460        4.814220          61.544680           2.085975                       15.607743        182.728999            29.959776      5.960068  2.128594  3.458577                5.064767            1.569490e+06             96.093574                 9.78859                   9.668642               9.849099                     9.839259                9.764633             9.644022  37201.194409  4.703702e+10           426816.294118         44.309320         1674.493416                16.846601        27.007161       60.433073        226.456566          226.456566  5681.651334     3576.190089     4471.877255        895.687166              0.290819      2435.825413      3204.936722         769.111309               0.359081            1505.195934            2109.676493               604.480559                          inf        0.571651        0.651354            0.079703          1.520866   
1         True  2447.330601  2.787199e+07  9.531881e+07  36.178017 -86.774374  205.651184        4.234973          72.710383           2.069426                       14.808743        189.396175            27.113036      7.293260  2.543256  4.268004                4.395082            8.699029e+02             97.131387                 9.88000                   9.734884               9.913408                     9.889302                9.597765             9.723464  37208.071949  4.703701e+10           351392.434426         60.111093         1609.426829                26.412300        11.371831       14.857277        139.952641          139.952641  4154.852459     3533.493625     4200.807832        667.314208              0.266878      2252.191257      3158.864299         906.673042               0.444095            1456.461749            1954.929872               498.468124                     0.340938        0.369828        0.587570            0.217742          1.183004   

   bach_pct_2010  bach_pct_2019  bach_value_change  bach_pct_change  rent_pct_2010  rent_pct_2019  rent_value_change  renter_pct_change  median_hhi_2010  median_hhi_2019  median_hhi_value_change  median_hhi_pct_change  poverty_pct_2010  poverty_pct_2019  poverty_value_change  poverty_pct_change  
0       0.357637       0.499072           0.141435         0.498359       0.532690       0.578225           0.045321           0.148095     40089.430389     61471.520377             21359.946510               0.584265         18.175872         18.030705             -0.135989            0.890558  
1       0.196196       0.446576           0.250380         1.656627       0.545858       0.517953          -0.027906          -0.046680     27587.212204     62067.497268             34480.285064               1.348760         28.506375         19.173588             -9.332787           -0.307604

In [ ]:
#airbnb.to_csv('../data/airbnb_gentrification.csv', index=False)

## Prepare Data for EDA Visuals

In [12]:
airbnb_identifying_list = ['house_pct_change', 'rental_price_pct_change', 'white_pct_change', 
                      'bach_pct_change', 'renter_pct_change', 'median_hhi_pct_change', 'poverty_pct_change',
                     'gentrifying']

In [13]:
airbnb_neighborhood_list = ['new_restaurants', 'available_beer', 'str_permits_growth', 'crimes',
                             'total_pop_pct_change', 'price', 'availability_365', 'accommodates', 'gentrifying']

In [170]:
airbnb_ratings_list = ['review_scores_cleanliness', 'review_scores_checkin', 'review_scores_communication', 
                      'review_scores_value', 'review_scores_location', 'review_scores_rating', 'gentrifying']

In [15]:
airbnb_identifying = airbnb_means[airbnb_identifying_list]
airbnb_identifying['house_pct_change'] = airbnb_identifying['house_pct_change'] / 100
airbnb_identifying['rental_price_pct_change'] = airbnb_identifying['rental_price_pct_change'] / 100

In [16]:
airbnb_identifying

house_pct_change  rental_price_pct_change  white_pct_change  bach_pct_change  renter_pct_change  median_hhi_pct_change  poverty_pct_change  gentrifying
0          0.522581                 0.177933          0.724861         0.284289           0.239182               0.340012            1.314106        False
1          0.610180                 0.259417          1.265029         1.891803          -0.027578               1.079066           -0.329638         True

In [17]:
airbnb_identifying.columns

Index(['house_pct_change', 'rental_price_pct_change', 'white_pct_change', 'bach_pct_change', 'renter_pct_change', 'median_hhi_pct_change', 'poverty_pct_change', 'gentrifying'], dtype='object')

In [29]:
airbnb_identifying_df = pd.melt(
    airbnb_identifying,
    id_vars = 'gentrifying',
    value_vars = ['house_pct_change', 'rental_price_pct_change', 'white_pct_change', 'bach_pct_change', 
                  'renter_pct_change', 'median_hhi_pct_change', 'poverty_pct_change'])

airbnb_identifying_df

gentrifying                 variable     value
0         False         house_pct_change  0.522581
1          True         house_pct_change  0.610180
2         False  rental_price_pct_change  0.177933
3          True  rental_price_pct_change  0.259417
4         False         white_pct_change  0.724861
5          True         white_pct_change  1.265029
6         False          bach_pct_change  0.284289
7          True          bach_pct_change  1.891803
8         False        renter_pct_change  0.239182
9          True        renter_pct_change -0.027578
10        False    median_hhi_pct_change  0.340012
11         True    median_hhi_pct_change  1.079066
12        False       poverty_pct_change  1.314106
13         True       poverty_pct_change -0.329638

In [30]:
airbnb_neighborhood_features = airbnb_medians[airbnb_neighborhood_list]

In [31]:
airbnb_neighborhood_features

new_restaurants  available_beer  str_permits_growth  crimes  total_pop_pct_change  price  availability_365  accommodates  gentrifying
0              3.0             4.0                 9.0  1958.0              0.100704   98.5             180.0           4.0        False
1              4.0             6.0                68.0  3457.0              0.039002   94.0             199.0           6.0         True

In [32]:
airbnb_neighborhood_features.columns

Index(['new_restaurants', 'available_beer', 'str_permits_growth', 'crimes', 'total_pop_pct_change', 'price', 'availability_365', 'accommodates', 'gentrifying'], dtype='object')

In [33]:
airbnb_neighborhood_df = pd.melt(
    airbnb_neighborhood_features,
    id_vars = 'gentrifying',
    value_vars = ['new_restaurants', 'available_beer', 'str_permits_growth', 'crimes', 'total_pop_pct_change', 
                  'price', 'availability_365', 'accommodates'])

airbnb_neighborhood_df

gentrifying              variable        value
0         False       new_restaurants     3.000000
1          True       new_restaurants     4.000000
2         False        available_beer     4.000000
3          True        available_beer     6.000000
4         False    str_permits_growth     9.000000
5          True    str_permits_growth    68.000000
6         False                crimes  1958.000000
7          True                crimes  3457.000000
8         False  total_pop_pct_change     0.100704
9          True  total_pop_pct_change     0.039002
10        False                 price    98.500000
11         True                 price    94.000000
12        False      availability_365   180.000000
13         True      availability_365   199.000000
14        False          accommodates     4.000000
15         True          accommodates     6.000000

In [171]:
airbnb_ratings = airbnb_means[airbnb_ratings_list]
airbnb_ratings['review_scores_rating'] = airbnb_ratings['review_scores_rating']/10

In [172]:
airbnb_ratings

review_scores_cleanliness  review_scores_checkin  review_scores_communication  review_scores_value  review_scores_location  review_scores_rating  gentrifying
0                   9.668642               9.849099                     9.839259             9.644022                9.764633              9.609357        False
1                   9.734884               9.913408                     9.889302             9.723464                9.597765              9.713139         True

In [173]:
airbnb_ratings.columns

Index(['review_scores_cleanliness', 'review_scores_checkin', 'review_scores_communication', 'review_scores_value', 'review_scores_location', 'review_scores_rating', 'gentrifying'], dtype='object')

In [174]:
airbnb_ratings_df = pd.melt(
    airbnb_ratings,
    id_vars = 'gentrifying',
    value_vars = ['review_scores_cleanliness', 'review_scores_checkin', 'review_scores_communication', 
                  'review_scores_value', 'review_scores_location', 'review_scores_rating'])

airbnb_ratings_df

gentrifying                     variable     value
0         False    review_scores_cleanliness  9.668642
1          True    review_scores_cleanliness  9.734884
2         False        review_scores_checkin  9.849099
3          True        review_scores_checkin  9.913408
4         False  review_scores_communication  9.839259
5          True  review_scores_communication  9.889302
6         False          review_scores_value  9.644022
7          True          review_scores_value  9.723464
8         False       review_scores_location  9.764633
9          True       review_scores_location  9.597765
10        False         review_scores_rating  9.609357
11         True         review_scores_rating  9.713139

## EDA Visuals

In [38]:
df = airbnb_identifying_df

identifying_plot = px.bar(df, x="variable", y="value",
             color='gentrifying', barmode='group',
             height=400)
identifying_plot.show()

# identifying_plot.write_html(
#     "/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/identifying_plot.html")
# py.plot(identifying_plot, filename = 'identifying_plot', auto_open=True)

'https://plotly.com/~matttparker/24/'

In [175]:
df = airbnb_ratings_df

ratings_plot = px.bar(df, x="variable", y="value",
             color='gentrifying', barmode='group',
             range_y = (9, 10), height=400)
ratings_plot.show()

# ratings_plot.write_html(
#     "/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/ratings_plot.html")
# py.plot(ratings_plot, filename = 'ratings_plot', auto_open=True)

'https://plotly.com/~matttparker/26/'

## Post-NLP Examination and Visualizations

In [40]:
tracts_rankings = gpd.read_file('../data/tracts_rankings.shp')

In [41]:
tracts_rankings.head()

GEOID  house_pct_  rental_pri  white_pct_  bach_pct_c  renter_pct  median_hhi  poverty_pc  total_rank  gentrifyin                                           geometry
0  47037015625        31.0        29.0        71.0       141.0       127.0       110.0        99.0       104.0           0  POLYGON ((-86.65754 36.11937, -86.65558 36.122...
1  47037016000         1.0        37.0         4.0         6.0       136.0         2.0        53.0         8.0           1  POLYGON ((-86.77265 36.14987, -86.76948 36.151...
2  47037017300         1.0        37.0        21.0         2.0       104.0        43.0        48.0        11.0           1  POLYGON ((-86.75091 36.12039, -86.75051 36.121...
3  47037018409         NaN         NaN         NaN         NaN         NaN         NaN         NaN       150.0           0  POLYGON ((-86.98225 36.07529, -86.98171 36.075...
4  47037019106        73.0       123.0       113.0        70.0        83.0       116.0       120.0       138.0           0  POLYGON ((-86.74414 36.04342, -86.74375 36.047...

In [42]:
tracts_rankings.columns = ['GEOID', 'house_pct_change_rank', 'rental_price_pct_change_rank', 
                           'white_pct_change_rank', 'bach_pct_change_rank', 'renter_pct_change_rank', 
                           'median_hhi_pct_change_rank', 'poverty_pct_change_rank', 'total_rank', 'gentrifying', 
                           'geometry']

In [44]:
tracts_rankings.shape

(161, 11)

In [45]:
tracts_rankings.GEOID = tracts_rankings.GEOID.astype(str)

In [46]:
# Read topic df from mp04 and merge to tracts df
airbnb_topics = pd.read_csv('../data/airbnb_topics_df.csv')

In [47]:
airbnb_topics

listing_id  topic         GEOID
0         6422.0      1  4.703701e+10
1        25613.0      1  4.703701e+10
2       136015.0      6  4.703702e+10
3       258817.0      1  4.703702e+10
4       289242.0      1  4.703702e+10
...          ...    ...           ...
5367  48068760.0      3  4.703702e+10
5368  48095829.0      5  4.703702e+10
5369  48095943.0      5  4.703702e+10
5370  48108210.0      5  4.703701e+10
5371  48130048.0      5  4.703702e+10

[5372 rows x 3 columns]

In [48]:
airbnb_topics = airbnb_topics[airbnb_topics['listing_id'].notna()]
airbnb_topics = airbnb_topics[airbnb_topics['GEOID'].notna()]

In [49]:
airbnb_topics['listing_id'] = airbnb_topics['listing_id'].astype(int).astype(str)
airbnb_topics['GEOID'] = airbnb_topics['GEOID'].astype(int).astype(str)

In [51]:
airbnb_topics['str_count'] = airbnb_topics.groupby('GEOID')['GEOID'].transform('size')
#airbnb_topics['topic_count'] = airbnb_topics.groupby('GEOID')['topic'].transform(pd.Series.value_counts)

In [52]:
airbnb_topics

listing_id  topic        GEOID  str_count
0          6422      1  47037012200         81
1         25613      1  47037012100         75
2        136015      6  47037015300        139
3        258817      1  47037015610         24
4        289242      1  47037015610         24
...         ...    ...          ...        ...
5367   48068760      3  47037015900          9
5368   48095829      5  47037015803         15
5369   48095943      5  47037015803         15
5370   48108210      5  47037013300         63
5371   48130048      5  47037015803         15

[5192 rows x 4 columns]

In [53]:
airbnb_topics_grouped = airbnb_topics.groupby(['GEOID', 'str_count', 'topic'])['listing_id'].count().reset_index()
airbnb_topics_grouped

GEOID  str_count  topic  listing_id
0    47037010105          3      0           1
1    47037010105          3      7           2
2    47037010106          4      0           2
3    47037010106          4      7           2
4    47037010201          3      0           1
..           ...        ...    ...         ...
663  47037019600         37      5           9
664  47037019600         37      6           1
665  47037019600         37      7          15
666  47037980100          4      3           1
667  47037980100          4      5           3

[668 rows x 4 columns]

In [54]:
airbnb_topics_grouped = airbnb_topics_grouped.rename(columns={'listing_id':'topic_count'})

In [55]:
airbnb_topics_grouped['pct_topic'] = airbnb_topics_grouped['topic_count'] / airbnb_topics_grouped['str_count']

In [56]:
airbnb_topics_grouped

GEOID  str_count  topic  topic_count  pct_topic
0    47037010105          3      0            1   0.333333
1    47037010105          3      7            2   0.666667
2    47037010106          4      0            2   0.500000
3    47037010106          4      7            2   0.500000
4    47037010201          3      0            1   0.333333
..           ...        ...    ...          ...        ...
663  47037019600         37      5            9   0.243243
664  47037019600         37      6            1   0.027027
665  47037019600         37      7           15   0.405405
666  47037980100          4      3            1   0.250000
667  47037980100          4      5            3   0.750000

[668 rows x 5 columns]

In [57]:
tracts_rankings

GEOID  house_pct_change_rank  rental_price_pct_change_rank  white_pct_change_rank  bach_pct_change_rank  renter_pct_change_rank  median_hhi_pct_change_rank  poverty_pct_change_rank  total_rank  gentrifying                                           geometry
0    47037015625                   31.0                          29.0                   71.0                 141.0                   127.0                       110.0                     99.0       104.0            0  POLYGON ((-86.65754 36.11937, -86.65558 36.122...
1    47037016000                    1.0                          37.0                    4.0                   6.0                   136.0                         2.0                     53.0         8.0            1  POLYGON ((-86.77265 36.14987, -86.76948 36.151...
2    47037017300                    1.0                          37.0                   21.0                   2.0                   104.0                        43.0                     48.0        11.0            1  POLYGON ((-86.75091 36.12039, -86.75051 36.121...
3    47037018409                    NaN                           NaN                    NaN                   NaN                     NaN                         NaN                      NaN       150.0            0  POLYGON ((-86.98225 36.07529, -86.98171 36.075...
4    47037019106                   73.0                         123.0                  113.0                  70.0                    83.0                       116.0                    120.0       138.0            0  POLYGON ((-86.74414 36.04342, -86.74375 36.047...
..           ...                    ...                           ...                    ...                   ...                     ...                         ...                      ...         ...          ...                                                ...
156  47037019004                   73.0                         123.0                  144.0                  73.0                    81.0                        50.0                     56.0       102.0            0  POLYGON ((-86.72632 36.07961, -86.72316 36.080...
157  47037010105                   46.0                          37.0                  142.0                 113.0                     1.0                       106.0                     29.0        63.0            0  POLYGON ((-86.88999 36.26282, -86.88760 36.265...
158  47037010904                    1.0                           1.0                   38.0                   9.0                    55.0                       150.0                     73.0        27.0            0  POLYGON ((-86.78634 36.23793, -86.78518 36.238...
159  47037018901                   73.0                         123.0                   85.0                 129.0                    23.0                        90.0                     46.0        97.0            0  POLYGON ((-86.76002 36.08151, -86.75783 36.083...
160  47037019116                   73.0                         123.0                   97.0                 145.0                    77.0                       129.0                    117.0       143.0            0  POLYGON ((-86.74355 36.03443, -86.74351 36.040...

[161 rows x 11 columns]

## Create map with boolean gentrifying tracts highlighted

In [62]:
tracts_rankings.head(1)

GEOID  house_pct_change_rank  rental_price_pct_change_rank  white_pct_change_rank  bach_pct_change_rank  renter_pct_change_rank  median_hhi_pct_change_rank  poverty_pct_change_rank  total_rank  gentrifying                                           geometry
0  47037015625                   31.0                          29.0                   71.0                 141.0                   127.0                       110.0                     99.0       104.0            0  POLYGON ((-86.65754 36.11937, -86.65558 36.122...

In [66]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

gentrifying_map = px.choropleth(tracts_rankings, 
                    geojson=tracts_rankings.geometry,
                    locations=tracts_rankings.index, 
                    color='gentrifying',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
gentrifying_map.update_geos(fitbounds="locations", visible=False)

gentrifying_map.show()

# gentrifying_map.write_html(
#     "/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/gentrifying_map.html")
# py.plot(gentrifying_map, filename = 'gentrifying_map', auto_open=True)

In [67]:
tracts_vis = tracts_rankings.copy()
tracts_vis = tracts_vis[['GEOID', 'geometry', 'gentrifying']]

In [68]:
topic_1_df = airbnb_topics_grouped[airbnb_topics_grouped['topic']==0]
topic_1_df = tracts_vis.merge(topic_1_df, on='GEOID', how='left')
topic_1_df['pct_topic'] = topic_1_df['pct_topic'].fillna(0)
topic_1_df

GEOID                                           geometry  gentrifying  str_count  topic  topic_count  pct_topic
0    47037015625  POLYGON ((-86.65754 36.11937, -86.65558 36.122...            0       26.0    0.0          6.0   0.230769
1    47037016000  POLYGON ((-86.77265 36.14987, -86.76948 36.151...            1       67.0    0.0         44.0   0.656716
2    47037017300  POLYGON ((-86.75091 36.12039, -86.75051 36.121...            1       31.0    0.0         10.0   0.322581
3    47037018409  POLYGON ((-86.98225 36.07529, -86.98171 36.075...            0        NaN    NaN          NaN   0.000000
4    47037019106  POLYGON ((-86.74414 36.04342, -86.74375 36.047...            0        NaN    NaN          NaN   0.000000
..           ...                                                ...          ...        ...    ...          ...        ...
156  47037019004  POLYGON ((-86.72632 36.07961, -86.72316 36.080...            0        7.0    0.0          1.0   0.142857
157  47037010105  POLYGON ((-86.88999 36.26282, -86.88760 36.265...            0        3.0    0.0          1.0   0.333333
158  47037010904  POLYGON ((-86.78634 36.23793, -86.78518 36.238...            0        4.0    0.0          1.0   0.250000
159  47037018901  POLYGON ((-86.76002 36.08151, -86.75783 36.083...            0       17.0    0.0          2.0   0.117647
160  47037019116  POLYGON ((-86.74355 36.03443, -86.74351 36.040...            0       15.0    0.0          2.0   0.133333

[161 rows x 7 columns]

In [ ]:
topic_0_df = airbnb_topics_grouped[airbnb_topics_grouped['topic']==0]
topic_0_df = tracts_vis.merge(topic_0_df, on='GEOID', how='left')
topic_0_df['pct_topic'] = topic_0_df['pct_topic'].fillna(0)
topic_0_df

In [ ]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

topic_0_map = px.choropleth(topic_0_df, 
                    geojson=topic_0_df.geometry,
                    locations=topic_0_df.index, 
                    color='pct_topic',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
topic_0_map.update_geos(fitbounds="locations", visible=False)

topic_0_map.show()

# topic_0_map.write_html("/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_0_map.html")
# py.plot(topic_0_map, filename = 'topic_0_map', auto_open=True)

In [69]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

topic_1_map = px.choropleth(topic_1_df, 
                    geojson=topic_1_df.geometry,
                    locations=topic_1_df.index, 
                    color='pct_topic',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
topic_1_map.update_geos(fitbounds="locations", visible=False)

topic_1_map.show()

# topic_1_map.write_html("/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_1_map.html")
# py.plot(topic_1_map, filename = 'topic_1_map', auto_open=True)

'https://plotly.com/~matttparker/42/'

In [70]:
topic_2_df = airbnb_topics_grouped[airbnb_topics_grouped['topic']==1]
topic_2_df = tracts_vis.merge(topic_2_df, on='GEOID', how='left')
topic_2_df['pct_topic'] = topic_2_df['pct_topic'].fillna(0)
topic_2_df

GEOID                                           geometry  gentrifying  str_count  topic  topic_count  pct_topic
0    47037015625  POLYGON ((-86.65754 36.11937, -86.65558 36.122...            0       26.0    1.0          1.0   0.038462
1    47037016000  POLYGON ((-86.77265 36.14987, -86.76948 36.151...            1        NaN    NaN          NaN   0.000000
2    47037017300  POLYGON ((-86.75091 36.12039, -86.75051 36.121...            1       31.0    1.0          1.0   0.032258
3    47037018409  POLYGON ((-86.98225 36.07529, -86.98171 36.075...            0        NaN    NaN          NaN   0.000000
4    47037019106  POLYGON ((-86.74414 36.04342, -86.74375 36.047...            0        5.0    1.0          2.0   0.400000
..           ...                                                ...          ...        ...    ...          ...        ...
156  47037019004  POLYGON ((-86.72632 36.07961, -86.72316 36.080...            0        NaN    NaN          NaN   0.000000
157  47037010105  POLYGON ((-86.88999 36.26282, -86.88760 36.265...            0        NaN    NaN          NaN   0.000000
158  47037010904  POLYGON ((-86.78634 36.23793, -86.78518 36.238...            0        NaN    NaN          NaN   0.000000
159  47037018901  POLYGON ((-86.76002 36.08151, -86.75783 36.083...            0        NaN    NaN          NaN   0.000000
160  47037019116  POLYGON ((-86.74355 36.03443, -86.74351 36.040...            0       15.0    1.0          1.0   0.066667

[161 rows x 7 columns]

In [72]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

topic_2_map = px.choropleth(topic_2_df, 
                    geojson=topic_2_df.geometry,
                    locations=topic_2_df.index, 
                    color='pct_topic',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
topic_2_map.update_geos(fitbounds="locations", visible=False)

topic_2_map.show()

# topic_2_map.write_html("/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_2_map.html")
# py.plot(topic_2_map, filename = 'topic_2_map', auto_open=True)

'https://plotly.com/~matttparker/44/'

In [73]:
topic_3_df = airbnb_topics_grouped[airbnb_topics_grouped['topic']==2]
topic_3_df = tracts_vis.merge(topic_3_df, on='GEOID', how='left')
topic_3_df['pct_topic'] = topic_3_df['pct_topic'].fillna(0)
topic_3_df

GEOID                                           geometry  gentrifying  str_count  topic  topic_count  pct_topic
0    47037015625  POLYGON ((-86.65754 36.11937, -86.65558 36.122...            0        NaN    NaN          NaN   0.000000
1    47037016000  POLYGON ((-86.77265 36.14987, -86.76948 36.151...            1        NaN    NaN          NaN   0.000000
2    47037017300  POLYGON ((-86.75091 36.12039, -86.75051 36.121...            1        NaN    NaN          NaN   0.000000
3    47037018409  POLYGON ((-86.98225 36.07529, -86.98171 36.075...            0        NaN    NaN          NaN   0.000000
4    47037019106  POLYGON ((-86.74414 36.04342, -86.74375 36.047...            0        NaN    NaN          NaN   0.000000
..           ...                                                ...          ...        ...    ...          ...        ...
156  47037019004  POLYGON ((-86.72632 36.07961, -86.72316 36.080...            0        NaN    NaN          NaN   0.000000
157  47037010105  POLYGON ((-86.88999 36.26282, -86.88760 36.265...            0        NaN    NaN          NaN   0.000000
158  47037010904  POLYGON ((-86.78634 36.23793, -86.78518 36.238...            0        NaN    NaN          NaN   0.000000
159  47037018901  POLYGON ((-86.76002 36.08151, -86.75783 36.083...            0        NaN    NaN          NaN   0.000000
160  47037019116  POLYGON ((-86.74355 36.03443, -86.74351 36.040...            0       15.0    2.0          1.0   0.066667

[161 rows x 7 columns]

In [74]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

topic_3_map = px.choropleth(topic_3_df, 
                    geojson=topic_3_df.geometry,
                    locations=topic_3_df.index, 
                    color='pct_topic',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
topic_3_map.update_geos(fitbounds="locations", visible=False)

topic_3_map.show()

# topic_3_map.write_html("/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_3_map.html")
# py.plot(topic_3_map, filename = 'topic_3_map', auto_open=True)

'https://plotly.com/~matttparker/46/'

In [75]:
topic_4_df = airbnb_topics_grouped[airbnb_topics_grouped['topic']==3]
topic_4_df = tracts_vis.merge(topic_4_df, on='GEOID', how='left')
topic_4_df['pct_topic'] = topic_4_df['pct_topic'].fillna(0)
topic_4_df

GEOID                                           geometry  gentrifying  str_count  topic  topic_count  pct_topic
0    47037015625  POLYGON ((-86.65754 36.11937, -86.65558 36.122...            0       26.0    3.0          1.0   0.038462
1    47037016000  POLYGON ((-86.77265 36.14987, -86.76948 36.151...            1       67.0    3.0          5.0   0.074627
2    47037017300  POLYGON ((-86.75091 36.12039, -86.75051 36.121...            1       31.0    3.0          4.0   0.129032
3    47037018409  POLYGON ((-86.98225 36.07529, -86.98171 36.075...            0        NaN    NaN          NaN   0.000000
4    47037019106  POLYGON ((-86.74414 36.04342, -86.74375 36.047...            0        NaN    NaN          NaN   0.000000
..           ...                                                ...          ...        ...    ...          ...        ...
156  47037019004  POLYGON ((-86.72632 36.07961, -86.72316 36.080...            0        NaN    NaN          NaN   0.000000
157  47037010105  POLYGON ((-86.88999 36.26282, -86.88760 36.265...            0        NaN    NaN          NaN   0.000000
158  47037010904  POLYGON ((-86.78634 36.23793, -86.78518 36.238...            0        NaN    NaN          NaN   0.000000
159  47037018901  POLYGON ((-86.76002 36.08151, -86.75783 36.083...            0       17.0    3.0          4.0   0.235294
160  47037019116  POLYGON ((-86.74355 36.03443, -86.74351 36.040...            0       15.0    3.0          2.0   0.133333

[161 rows x 7 columns]

In [76]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

topic_4_map = px.choropleth(topic_4_df, 
                    geojson=topic_4_df.geometry,
                    locations=topic_4_df.index, 
                    color='pct_topic',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
topic_4_map.update_geos(fitbounds="locations", visible=False)

topic_4_map.show()

# topic_4_map.write_html("/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_4_map.html")
# py.plot(topic_4_map, filename = 'topic_4_map', auto_open=True)

'https://plotly.com/~matttparker/48/'

In [77]:
topic_5_df = airbnb_topics_grouped[airbnb_topics_grouped['topic']==4]
topic_5_df = tracts_vis.merge(topic_5_df, on='GEOID', how='left')
topic_5_df['pct_topic'] = topic_5_df['pct_topic'].fillna(0)
topic_5_df

GEOID                                           geometry  gentrifying  str_count  topic  topic_count  pct_topic
0    47037015625  POLYGON ((-86.65754 36.11937, -86.65558 36.122...            0        NaN    NaN          NaN   0.000000
1    47037016000  POLYGON ((-86.77265 36.14987, -86.76948 36.151...            1       67.0    4.0          2.0   0.029851
2    47037017300  POLYGON ((-86.75091 36.12039, -86.75051 36.121...            1        NaN    NaN          NaN   0.000000
3    47037018409  POLYGON ((-86.98225 36.07529, -86.98171 36.075...            0        NaN    NaN          NaN   0.000000
4    47037019106  POLYGON ((-86.74414 36.04342, -86.74375 36.047...            0        5.0    4.0          2.0   0.400000
..           ...                                                ...          ...        ...    ...          ...        ...
156  47037019004  POLYGON ((-86.72632 36.07961, -86.72316 36.080...            0        NaN    NaN          NaN   0.000000
157  47037010105  POLYGON ((-86.88999 36.26282, -86.88760 36.265...            0        NaN    NaN          NaN   0.000000
158  47037010904  POLYGON ((-86.78634 36.23793, -86.78518 36.238...            0        NaN    NaN          NaN   0.000000
159  47037018901  POLYGON ((-86.76002 36.08151, -86.75783 36.083...            0        NaN    NaN          NaN   0.000000
160  47037019116  POLYGON ((-86.74355 36.03443, -86.74351 36.040...            0       15.0    4.0          1.0   0.066667

[161 rows x 7 columns]

In [79]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

topic_5_map = px.choropleth(topic_5_df, 
                    geojson=topic_5_df.geometry,
                    locations=topic_5_df.index, 
                    color='pct_topic',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
topic_5_map.update_geos(fitbounds="locations", visible=False)

topic_5_map.show()

# topic_5_map.write_html("/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_5_map.html")
# py.plot(topic_5_map, filename = 'topic_5_map', auto_open=True)

'https://plotly.com/~matttparker/50/'

In [80]:
topic_6_df = airbnb_topics_grouped[airbnb_topics_grouped['topic']==5]
topic_6_df = tracts_vis.merge(topic_6_df, on='GEOID', how='left')
topic_6_df['pct_topic'] = topic_6_df['pct_topic'].fillna(0)
topic_6_df

GEOID                                           geometry  gentrifying  str_count  topic  topic_count  pct_topic
0    47037015625  POLYGON ((-86.65754 36.11937, -86.65558 36.122...            0        NaN    NaN          NaN   0.000000
1    47037016000  POLYGON ((-86.77265 36.14987, -86.76948 36.151...            1       67.0    5.0          6.0   0.089552
2    47037017300  POLYGON ((-86.75091 36.12039, -86.75051 36.121...            1       31.0    5.0          1.0   0.032258
3    47037018409  POLYGON ((-86.98225 36.07529, -86.98171 36.075...            0        NaN    NaN          NaN   0.000000
4    47037019106  POLYGON ((-86.74414 36.04342, -86.74375 36.047...            0        NaN    NaN          NaN   0.000000
..           ...                                                ...          ...        ...    ...          ...        ...
156  47037019004  POLYGON ((-86.72632 36.07961, -86.72316 36.080...            0        NaN    NaN          NaN   0.000000
157  47037010105  POLYGON ((-86.88999 36.26282, -86.88760 36.265...            0        NaN    NaN          NaN   0.000000
158  47037010904  POLYGON ((-86.78634 36.23793, -86.78518 36.238...            0        4.0    5.0          1.0   0.250000
159  47037018901  POLYGON ((-86.76002 36.08151, -86.75783 36.083...            0        NaN    NaN          NaN   0.000000
160  47037019116  POLYGON ((-86.74355 36.03443, -86.74351 36.040...            0       15.0    5.0          1.0   0.066667

[161 rows x 7 columns]

In [81]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

topic_6_map = px.choropleth(topic_6_df, 
                    geojson=topic_6_df.geometry,
                    locations=topic_6_df.index, 
                    color='pct_topic',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
topic_6_map.update_geos(fitbounds="locations", visible=False)

topic_6_map.show()

# topic_6_map.write_html("/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_6_map.html")
# py.plot(topic_6_map, filename = 'topic_6_map', auto_open=True)

'https://plotly.com/~matttparker/52/'

In [82]:
topic_7_df = airbnb_topics_grouped[airbnb_topics_grouped['topic']==6]
topic_7_df = tracts_vis.merge(topic_7_df, on='GEOID', how='left')
topic_7_df['pct_topic'] = topic_7_df['pct_topic'].fillna(0)
topic_7_df

GEOID                                           geometry  gentrifying  str_count  topic  topic_count  pct_topic
0    47037015625  POLYGON ((-86.65754 36.11937, -86.65558 36.122...            0       26.0    6.0          4.0   0.153846
1    47037016000  POLYGON ((-86.77265 36.14987, -86.76948 36.151...            1       67.0    6.0          1.0   0.014925
2    47037017300  POLYGON ((-86.75091 36.12039, -86.75051 36.121...            1        NaN    NaN          NaN   0.000000
3    47037018409  POLYGON ((-86.98225 36.07529, -86.98171 36.075...            0        NaN    NaN          NaN   0.000000
4    47037019106  POLYGON ((-86.74414 36.04342, -86.74375 36.047...            0        NaN    NaN          NaN   0.000000
..           ...                                                ...          ...        ...    ...          ...        ...
156  47037019004  POLYGON ((-86.72632 36.07961, -86.72316 36.080...            0        NaN    NaN          NaN   0.000000
157  47037010105  POLYGON ((-86.88999 36.26282, -86.88760 36.265...            0        NaN    NaN          NaN   0.000000
158  47037010904  POLYGON ((-86.78634 36.23793, -86.78518 36.238...            0        NaN    NaN          NaN   0.000000
159  47037018901  POLYGON ((-86.76002 36.08151, -86.75783 36.083...            0       17.0    6.0          2.0   0.117647
160  47037019116  POLYGON ((-86.74355 36.03443, -86.74351 36.040...            0       15.0    6.0          2.0   0.133333

[161 rows x 7 columns]

In [84]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

topic_7_map = px.choropleth(topic_7_df, 
                    geojson=topic_7_df.geometry,
                    locations=topic_7_df.index, 
                    color='pct_topic',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
topic_7_map.update_geos(fitbounds="locations", visible=False)

topic_7_map.show()

# topic_7_map.write_html("/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_7_map.html")
# py.plot(topic_7_map, filename = 'topic_7_map', auto_open=True)

In [85]:
topic_8_df = airbnb_topics_grouped[airbnb_topics_grouped['topic']==7]
topic_8_df = tracts_vis.merge(topic_8_df, on='GEOID', how='left')
topic_8_df['pct_topic'] = topic_8_df['pct_topic'].fillna(0)
topic_8_df

GEOID                                           geometry  gentrifying  str_count  topic  topic_count  pct_topic
0    47037015625  POLYGON ((-86.65754 36.11937, -86.65558 36.122...            0       26.0    7.0         14.0   0.538462
1    47037016000  POLYGON ((-86.77265 36.14987, -86.76948 36.151...            1       67.0    7.0          9.0   0.134328
2    47037017300  POLYGON ((-86.75091 36.12039, -86.75051 36.121...            1       31.0    7.0         15.0   0.483871
3    47037018409  POLYGON ((-86.98225 36.07529, -86.98171 36.075...            0        NaN    NaN          NaN   0.000000
4    47037019106  POLYGON ((-86.74414 36.04342, -86.74375 36.047...            0        5.0    7.0          1.0   0.200000
..           ...                                                ...          ...        ...    ...          ...        ...
156  47037019004  POLYGON ((-86.72632 36.07961, -86.72316 36.080...            0        7.0    7.0          6.0   0.857143
157  47037010105  POLYGON ((-86.88999 36.26282, -86.88760 36.265...            0        3.0    7.0          2.0   0.666667
158  47037010904  POLYGON ((-86.78634 36.23793, -86.78518 36.238...            0        4.0    7.0          2.0   0.500000
159  47037018901  POLYGON ((-86.76002 36.08151, -86.75783 36.083...            0       17.0    7.0          9.0   0.529412
160  47037019116  POLYGON ((-86.74355 36.03443, -86.74351 36.040...            0       15.0    7.0          5.0   0.333333

[161 rows x 7 columns]

In [87]:
#percents_map[feature] = percents_map[feature].fillna(percents_map[feature].median())
colors = n_colors('rgb(0, 90, 220)', 'rgb(200, 15, 15)', 150, colortype='rgb')

topic_8_map = px.choropleth(topic_8_df, 
                    geojson=topic_8_df.geometry,
                    locations=topic_8_df.index, 
                    color='pct_topic',
                    color_continuous_scale=colors#,
#                       labels={'index': 'Census Tract',
#                         'total_rank': 'Overall Rank',
#                         'house_pct_change_rank':'Change in House Price',
#                         'rental_price_pct_change_rank': 'Change in Rental House Price',
#                         'white_pct_change_rank': 'Change in Percent White',
#                         'bach_pct_change_rank': 'Change in Percent with Bachelor Degree or Higher',
#                         'renter_pct_change_rank': 'Change in Percent Renting vs Owning Homes',
#                         'median_hhi_pct_change_rank': 'Change in Median Household Income',
#                         'poverty_pct_change_rank': 'Change in Percent under Poverty Level'},
#                     hover_data=['total_rank',
#                                 'house_pct_change_rank',
#                                'rental_price_pct_change_rank',
#                                'white_pct_change_rank',
#                                'bach_pct_change_rank',
#                                'renter_pct_change_rank',
#                                'median_hhi_pct_change_rank',
#                                'poverty_pct_change_rank']
                    )
topic_8_map.update_geos(fitbounds="locations", visible=False)

topic_8_map.show()

# topic_8_map.write_html("/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_8_map.html")
# py.plot(topic_8_map, filename = 'topic_8_map', auto_open=True)

## Examine neighborhood characteristics by Topic

In [144]:
airbnb_topics_full = pd.read_csv('../data/airbnb_topics_full.csv')

In [145]:
airbnb_topics_full = airbnb_topics_full[airbnb_topics_full['listing_id'].notna()]
airbnb_topics_full = airbnb_topics_full[airbnb_topics_full['GEOID'].notna()]

In [146]:
airbnb_topics_full['listing_id'] = airbnb_topics_full['listing_id'].astype(int).astype(str)
airbnb_topics_full['GEOID'] = airbnb_topics_full['GEOID'].astype(int).astype(str)

In [147]:
#airbnb_topics_full['percent'].hist()

In [148]:
airbnb_topics_full.head(1)

topic   percent listing_id                              comments_concatenated             name  host_id  latitude  longitude  price  minimum_nights  number_of_reviews  reviews_per_month  calculated_host_listings_count  availability_365                        listing_url                                        description                              neighborhood_overview  host_since  host_listings_count          property_type  accommodates  bathrooms_text  bedrooms  beds                                          amenities  minimum_nights_avg_ntm  maximum_nights_avg_ntm  review_scores_rating  review_scores_accuracy  review_scores_cleanliness  review_scores_checkin  review_scores_communication  review_scores_location  review_scores_value  zip_code        GEOID  house_price_2021-01-31  house_pct_change  rentals_2021-01-31  rental_price_pct_change  new_restaurants  available_beer  str_permits_2020  str_permits_growth  crimes  total_pop_2010  total_pop_2019  total_pop_change  \
0      1  0.509356       6422  I can't say enough about how wonderful it was ...  Nashville Charm  12172.0  36.17315  -86.73581   40.0            30.0              674.0               4.69                             1.0             267.0  https://www.airbnb.com/rooms/6422  30 day or more rental during COVID. Show COVID...  Historic East Nashville is home to many new an...  2009-04-03                  0.0  Private room in house           2.0  1 private bath       2.0   3.0  ["Hair dryer", "Bathtub", "Lock on bedroom doo...                    30.0                   365.0                  99.0                    10.0                       10.0                   10.0                         10.0                    10.0                 10.0   37206.0  47037012200                412476.0             38.31                 NaN                      NaN              1.0             2.0             114.0               114.0  1165.0          2544.0          2100.0            -444.0   

   total_pop_pct_change  pop_over25_2010  pop_over25_2019  pop_over25_change  pop_over25_pcg_change  total_households_2010  total_households_2019  total_households_change  total_households_pct_change  white_pct_2010  white_pct_2019  white_value_change  white_pct_change  bach_pct_2010  bach_pct_2019  bach_value_change  bach_pct_change  rent_pct_2010  rent_pct_2019  rent_value_change  renter_pct_change  median_hhi_2010  median_hhi_2019  median_hhi_value_change  median_hhi_pct_change  poverty_pct_2010  poverty_pct_2019  poverty_value_change  poverty_pct_change gentrifying  
0             -0.174528           1703.0           1639.0              -64.0              -0.037581                 1140.0                  926.0                   -214.0                    -0.187719        0.657626        0.940952            0.283327          0.430833       0.408691       0.585723           0.177032          0.43317       0.320175       0.240821          -0.079355          -0.247848          46000.0          91643.0                  45643.0               0.992239              10.6              10.2                  -0.4           -0.037736       False

In [149]:
#airbnb_topics_full.columns

In [150]:
airbnb_topics_full_list = ['topic', 'price', 'calculated_host_listings_count', 'property_type', 'accommodates', 
                           'review_scores_rating', 'review_scores_accuracy', 'review_scores_cleanliness', 
                           'review_scores_checkin', 'review_scores_communication', 'review_scores_location', 
                           'review_scores_value', 'GEOID', 'house_price_2021-01-31', 'house_pct_change', 
                           'rentals_2021-01-31', 'rental_price_pct_change', 'new_restaurants', 'available_beer', 
                           'str_permits_2020', 'crimes', 'total_pop_2019', 'total_pop_pct_change', 'white_pct_2019', 
                           'white_pct_change', 'bach_pct_2019', 'bach_pct_change', 'rent_pct_2019', 
                           'renter_pct_change', 'median_hhi_2019', 'median_hhi_pct_change', 'poverty_pct_2019', 
                           'poverty_pct_change', 'gentrifying']

In [151]:
airbnb_topics_full = airbnb_topics_full[airbnb_topics_full_list]

In [152]:
topics_means_list = ['topic', 'price', 'calculated_host_listings_count', 'accommodates', 'review_scores_rating', 
                     'review_scores_accuracy', 'review_scores_cleanliness', 'review_scores_checkin', 
                     'review_scores_communication', 'review_scores_location', 'review_scores_value', 
                     'new_restaurants', 'available_beer', 'crimes']

In [240]:
topics_means = airbnb_topics_full[topics_means_list].groupby('topic').mean()
topics_means

price  calculated_host_listings_count  accommodates  review_scores_rating  review_scores_accuracy  review_scores_cleanliness  review_scores_checkin  review_scores_communication  review_scores_location  review_scores_value  new_restaurants  available_beer        crimes
topic                                                                                                                                                                                                                                                                                   
0      307.245614                       23.929150      9.811741             97.601215                9.897904                   9.746450               9.937796                     9.925625                9.666667             9.784990        12.802353       25.099411   4059.502699
1      109.928571                        9.235714      3.492857             97.521429                9.828571                   9.714286               9.870504                     9.914286                9.762590             9.712230        14.870690       35.547619   4264.335714
2      195.094737                       15.452632      5.736842             95.050000                9.721519                   9.525000               9.662500                     9.737500                9.537500             9.367089        30.816092       70.340659   7423.347368
3      134.818328                        8.707395      4.614148             98.583601                9.952782                   9.920742               9.900506                     9.959528                9.870152             9.887015        22.867424       50.600352   5212.853698
4      153.605042                       12.416807      4.440336             97.885714                9.906250                   9.824653               9.930435                     9.949653                9.918261             9.768696        22.715342       48.060554   4724.927731
5      243.511443                       22.068657      5.195025             91.506468                9.442116                   9.311377               9.562874                     9.531936                9.572854             9.193613        53.294691      126.838006  10875.224876
6      222.993485                       10.319218      6.270358             97.671010                9.894737                   9.825658               9.871711                     9.901316                9.838816             9.799342        11.178261       26.801444   3091.947883
7      137.764271                        7.113108      4.453488             96.304440                9.854255                   9.672340               9.930851                     9.923404                9.715957             9.691489         8.473164       16.503623   3009.540169

In [241]:
airbnb_topics_full.mean()

topic                             3.479391e+00
price                             2.134104e+02
calculated_host_listings_count    1.600616e+01
accommodates                      6.249230e+00
review_scores_rating              9.629438e+01
review_scores_accuracy            9.803051e+00
review_scores_cleanliness         9.676965e+00
review_scores_checkin             9.847809e+00
review_scores_communication       9.850020e+00
review_scores_location            9.720070e+00
review_scores_value               9.654275e+00
GEOID                                      inf
house_price_2021-01-31            4.086874e+05
house_pct_change                  4.789799e+01
rentals_2021-01-31                1.660751e+03
rental_price_pct_change           1.932245e+01
new_restaurants                   2.333326e+01
available_beer                    5.110023e+01
str_permits_2020                  2.087563e+02
crimes                            5.411785e+03
total_pop_2019                    4.442680e+03
total_pop_pct

In [242]:
topics_medians_list = ['topic', 'house_price_2021-01-31', 'house_pct_change', 'rentals_2021-01-31', 
                       'rental_price_pct_change', 'total_pop_2019', 'total_pop_pct_change', 'white_pct_2019', 
                       'white_pct_change', 'bach_pct_2019', 'bach_pct_change', 'rent_pct_2019', 'renter_pct_change', 
                       'median_hhi_2019', 'median_hhi_pct_change', 'poverty_pct_2019', 'poverty_pct_change']

In [243]:
topics_medians = airbnb_topics_full[topics_medians_list].groupby('topic').median()
topics_medians

house_price_2021-01-31  house_pct_change  rentals_2021-01-31  rental_price_pct_change  total_pop_2019  total_pop_pct_change  white_pct_2019  white_pct_change  bach_pct_2019  bach_pct_change  rent_pct_2019  renter_pct_change  median_hhi_2019  median_hhi_pct_change  poverty_pct_2019  poverty_pct_change
topic                                                                                                                                                                                                                                                                                                               
0                    387583.0             45.78              1634.0                    22.49          3320.0              0.091701        0.547935          0.255900       0.398536         0.671050       0.588644           0.055159          50857.0               0.720376              20.3           -0.120879
1                    368932.0             49.19              1634.0                    22.18          4845.0              0.113288        0.686219          0.059186       0.469825         0.445325       0.460865           0.055159          63740.0               0.480956              15.5            0.008353
2                    385131.0             34.05              1630.0                    22.18          5810.0              0.583229        0.669707          0.403369       0.650122         0.763688       0.661002           0.055159          75446.0               0.776538              23.5           -0.105820
3                    387583.0             45.78              1682.0                    22.49          4037.0              0.102067        0.726891          0.188120       0.490000         0.668128       0.488906           0.064485          61250.0               0.698466              16.9           -0.105820
4                    412476.0             38.31              1630.0                     7.73          3897.0              0.209122        0.750670          0.182728       0.634017         0.433170       0.529291           0.089363          75446.0               0.772601              15.5           -0.105820
5                    459985.0             33.13              1745.0                    22.18          5304.0              0.613895        0.760458          0.403369       0.650122         0.671050       0.797233           0.114994          68889.0               0.776538              16.9           -0.105820
6                    368932.0             49.19              1682.0                    22.18          4068.0              0.091623        0.754664          0.039239       0.463522         0.387603       0.389892           0.078622          66008.0               0.446603              10.8            0.119403
7                    351685.0             51.35              1630.0                    22.18          4068.0              0.088371        0.717327          0.080004       0.399714         0.433170       0.461469           0.064485          56286.0               0.480203              15.5           -0.035088

In [244]:
#Find Number of units per Topic
airbnb_topics_full.groupby(['topic'])['gentrifying'].count()

topic
0    1482
1     140
2      95
3     622
4     595
5    1005
6     307
7     946
Name: gentrifying, dtype: int64

In [245]:
#Find % of units Gentrifying per Topic
airbnb_topics_full.groupby(['topic'])['gentrifying'].sum()

topic
0    529
1     23
2     41
3    174
4    104
5    160
6     58
7    215
Name: gentrifying, dtype: int64

In [246]:
#Find % of units Gentrifying per Topic
airbnb_topics_full.groupby(['topic'])['gentrifying'].sum().sum()

1304

## Comparison Ratings Charts: Topic vs Total

In [247]:
topics_means

price  calculated_host_listings_count  accommodates  review_scores_rating  review_scores_accuracy  review_scores_cleanliness  review_scores_checkin  review_scores_communication  review_scores_location  review_scores_value  new_restaurants  available_beer        crimes
topic                                                                                                                                                                                                                                                                                   
0      307.245614                       23.929150      9.811741             97.601215                9.897904                   9.746450               9.937796                     9.925625                9.666667             9.784990        12.802353       25.099411   4059.502699
1      109.928571                        9.235714      3.492857             97.521429                9.828571                   9.714286               9.870504                     9.914286                9.762590             9.712230        14.870690       35.547619   4264.335714
2      195.094737                       15.452632      5.736842             95.050000                9.721519                   9.525000               9.662500                     9.737500                9.537500             9.367089        30.816092       70.340659   7423.347368
3      134.818328                        8.707395      4.614148             98.583601                9.952782                   9.920742               9.900506                     9.959528                9.870152             9.887015        22.867424       50.600352   5212.853698
4      153.605042                       12.416807      4.440336             97.885714                9.906250                   9.824653               9.930435                     9.949653                9.918261             9.768696        22.715342       48.060554   4724.927731
5      243.511443                       22.068657      5.195025             91.506468                9.442116                   9.311377               9.562874                     9.531936                9.572854             9.193613        53.294691      126.838006  10875.224876
6      222.993485                       10.319218      6.270358             97.671010                9.894737                   9.825658               9.871711                     9.901316                9.838816             9.799342        11.178261       26.801444   3091.947883
7      137.764271                        7.113108      4.453488             96.304440                9.854255                   9.672340               9.930851                     9.923404                9.715957             9.691489         8.473164       16.503623   3009.540169

In [248]:
topics_means['review_scores_rating'] = topics_means['review_scores_rating'] / 10

In [249]:
topics_means_vis = pd.melt(
    topics_means.reset_index(),
    id_vars = 'topic',
    value_vars = ['review_scores_cleanliness', 'review_scores_checkin', 'review_scores_communication', 
                  'review_scores_value', 'review_scores_location', 'review_scores_rating'])
topics_means_vis['topic'] = topics_means_vis['topic'].astype(str)
topics_means_vis

topic                     variable     value
0      0    review_scores_cleanliness  9.746450
1      1    review_scores_cleanliness  9.714286
2      2    review_scores_cleanliness  9.525000
3      3    review_scores_cleanliness  9.920742
4      4    review_scores_cleanliness  9.824653
5      5    review_scores_cleanliness  9.311377
6      6    review_scores_cleanliness  9.825658
7      7    review_scores_cleanliness  9.672340
8      0        review_scores_checkin  9.937796
9      1        review_scores_checkin  9.870504
10     2        review_scores_checkin  9.662500
11     3        review_scores_checkin  9.900506
12     4        review_scores_checkin  9.930435
13     5        review_scores_checkin  9.562874
14     6        review_scores_checkin  9.871711
15     7        review_scores_checkin  9.930851
16     0  review_scores_communication  9.925625
17     1  review_scores_communication  9.914286
18     2  review_scores_communication  9.737500
19     3  review_scores_communication  9.959528
20     4  review_scores_communication  9.949653
21     5  review_scores_communication  9.531936
22     6  review_scores_communication  9.901316
23     7  review_scores_communication  9.923404
24     0          review_scores_value  9.784990
25     1          review_scores_value  9.712230
26     2          review_scores_value  9.367089
27     3          review_scores_value  9.887015
28     4          review_scores_value  9.768696
29     5          review_scores_value  9.193613
30     6          review_scores_value  9.799342
31     7          review_scores_value  9.691489
32     0       review_scores_location  9.666667
33     1       review_scores_location  9.762590
34     2       review_scores_location  9.537500
35     3       review_scores_location  9.870152
36     4       review_scores_location  9.918261
37     5       review_scores_location  9.572854
38     6       review_scores_location  9.838816
39     7       review_scores_location  9.715957
40     0         review_scores_rating  9.760121
41     1         review_scores_rating  9.752143
42     2         review_scores_rating  9.505000
43     3         review_scores_rating  9.858360
44     4         review_scores_rating  9.788571
45     5         review_scores_rating  9.150647
46     6         review_scores_rating  9.767101
47     7         review_scores_rating  9.630444

In [250]:
ratings_list = ['review_scores_rating','review_scores_accuracy', 'review_scores_cleanliness', 'review_scores_checkin', 
                     'review_scores_communication', 'review_scores_location', 'review_scores_value']

In [259]:
airbnb_topics_full_copy = airbnb_topics_full.copy()
airbnb_topics_full_copy['review_scores_rating'] = airbnb_topics_full_copy['review_scores_rating'] / 10

In [261]:
#Find mean of full dataset
topics_means_means = airbnb_topics_full_copy.mean().reset_index()
topics_means_means = topics_means_means[topics_means_means['index'].isin(ratings_list)]
topics_means_means.columns = ['variable', 'value']
topics_means_means['topic'] = ['all'] * 7
topics_means_means = topics_means_means[topics_means_means['variable']!='review_scores_accuracy']
topics_means_means

variable     value topic
4          review_scores_rating  9.629438   all
6     review_scores_cleanliness  9.676965   all
7         review_scores_checkin  9.847809   all
8   review_scores_communication  9.850020   all
9        review_scores_location  9.720070   all
10          review_scores_value  9.654275   all

In [262]:
topic_means_vis_df = topics_means_means.append(topics_means_vis, ignore_index=True)
topic_means_vis_df

variable     value topic
0          review_scores_rating  9.629438   all
1     review_scores_cleanliness  9.676965   all
2         review_scores_checkin  9.847809   all
3   review_scores_communication  9.850020   all
4        review_scores_location  9.720070   all
5           review_scores_value  9.654275   all
6     review_scores_cleanliness  9.746450     0
7     review_scores_cleanliness  9.714286     1
8     review_scores_cleanliness  9.525000     2
9     review_scores_cleanliness  9.920742     3
10    review_scores_cleanliness  9.824653     4
11    review_scores_cleanliness  9.311377     5
12    review_scores_cleanliness  9.825658     6
13    review_scores_cleanliness  9.672340     7
14        review_scores_checkin  9.937796     0
15        review_scores_checkin  9.870504     1
16        review_scores_checkin  9.662500     2
17        review_scores_checkin  9.900506     3
18        review_scores_checkin  9.930435     4
19        review_scores_checkin  9.562874     5
20        review_scores_checkin  9.871711     6
21        review_scores_checkin  9.930851     7
22  review_scores_communication  9.925625     0
23  review_scores_communication  9.914286     1
24  review_scores_communication  9.737500     2
25  review_scores_communication  9.959528     3
26  review_scores_communication  9.949653     4
27  review_scores_communication  9.531936     5
28  review_scores_communication  9.901316     6
29  review_scores_communication  9.923404     7
30          review_scores_value  9.784990     0
31          review_scores_value  9.712230     1
32          review_scores_value  9.367089     2
33          review_scores_value  9.887015     3
34          review_scores_value  9.768696     4
35          review_scores_value  9.193613     5
36          review_scores_value  9.799342     6
37          review_scores_value  9.691489     7
38       review_scores_location  9.666667     0
39       review_scores_location  9.762590     1
40       review_scores_location  9.537500     2
41       review_scores_location  9.870152     3
42       review_scores_location  9.918261     4
43       review_scores_location  9.572854     5
44       review_scores_location  9.838816     6
45       review_scores_location  9.715957     7
46         review_scores_rating  9.760121     0
47         review_scores_rating  9.752143     1
48         review_scores_rating  9.505000     2
49         review_scores_rating  9.858360     3
50         review_scores_rating  9.788571     4
51         review_scores_rating  9.150647     5
52         review_scores_rating  9.767101     6
53         review_scores_rating  9.630444     7

In [272]:
df = topic_means_vis_df[topic_means_vis_df['topic'].isin(['all', '7'])]

topic_plot = px.bar(df, x="variable", y="value",
             color='topic', barmode='group',
             range_y = (9, 10), height=400)
topic_plot.show()

topic_plot.write_html(
    "/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/topic_plot_8.html")
py.plot(topic_plot, filename = 'topic_plot_8', auto_open=True)

'https://plotly.com/~matttparker/76/'

## EDA Visuals

In [38]:
df = airbnb_identifying_df

identifying_plot = px.bar(df, x="variable", y="value",
             color='gentrifying', barmode='group',
             height=400)
identifying_plot.show()

# identifying_plot.write_html(
#     "/Users/mattparker/Documents/nss_projects/airbnb-sentiments/plotly_vis/identifying_plot.html")
# py.plot(identifying_plot, filename = 'identifying_plot', auto_open=True)

'https://plotly.com/~matttparker/24/'

### Failed Table Attempts

In [ ]:
x = gentrification_rank_table.columns.tolist(),
y = gentrification_rank_table.index.astype(int).astype(str).tolist()
z = gentrification_rank_table.values.tolist()

In [ ]:
df = gentrification_rank_table.reset_index()
z = df.values.tolist()

# change each element of z to type string for annotations
#z_text = [[str(y) for y in x] for x in z]
z_text = [[y for y in x] for x in z]

# set up figure 
fig = ff.create_annotated_heatmap(z, x=list(df.columns.astype(str)),
                                     y=list(df.index.astype(str)))#,
                                    # annotation_text=z_text, colorscale='agsunset')

# add title
fig.update_layout(title_text='<i><b>Confusion matrix</b></i>',
                  #xaxis = dict(title='x'),
                  #yaxis = dict(title='x')
                 )

# add custom xaxis title
fig.add_annotation(dict(font=dict(color="black",size=14),
                        x=0.5,
                        y=-0.15,
                        showarrow=False,
                        text="",
                        xref="paper",
                        yref="paper"))

# add custom yaxis title
fig.add_annotation(dict(font=dict(color="black",size=14),
                        x=-0.35,
                        y=0.5,
                        showarrow=False,
                        text="",
                        textangle=-90,
                        xref="paper",
                        yref="paper"))

# adjust margins to make room for yaxis title
fig.update_layout(margin=dict(t=50, l=200))

# add colorbar
fig['data'][0]['showscale'] = True
fig.show()

In [ ]:
fig = go.Figure(data=go.Heatmap(df_to_plotly(gentrification_rank_table)))
fig.show()

In [ ]:
gentrification_rank_table = gentrification_rank_counts.drop(
    columns='total').sort_values(
    'total_rank', ascending=True).head(20)

In [ ]:
tab = gentrification_rank_table.values.tolist()

In [ ]:
X = gentrification_rank_table.columns
Y = gentrification_rank_table.index

In [ ]:
trace =Heatmap(
        z=tab,
        x=X, 
        y=Y,
        colorscale='blues', 
        colorbar=dict(thickness=20, tickvals=[1,150], ticklen=30)
        )

# width = 900
# height =900

# layout = Layout(
#     title='ETFs Data', 
#     font=Font(
#         family='Balto, sans-serif',
#         size=12,
#         color='rgb(68,68,68)'
#     ),
#     showlegend=False,
#     xaxis=XAxis(
#         title='',  
#         showgrid=True,
#         side='top',
#         tickangle=45
#     ),
#     yaxis=YAxis(
#         title='',
#         autorange='reversed',
#         showgrid=True,   
#         tickmode='auto',  
#         nticks = 5          
#     ),
#     autosize=False, 
#     height=height,   
#     width=width,
#     margin=Margin(
#         l=135,
#         r=40,
#         b=85,
#         t=170
#     )
# )
   


fig=Figure(data=Data([trace]), layout=layout)        

annotations = Annotations()
alist=list(tab)
for i, row in enumerate(alist):
    for j, val in enumerate(row):
        annotations.append(
            Annotation(
                text=str(val), 
                x=X[j], y=Y[i],
                xref='x1', yref='y1',
                font=dict(color= 'rgb(25,25,25)'),
                showarrow=False))
fig['layout'].update(annotations=annotations)
                                              
fig.show()                                              

In [ ]:
colors = n_colors('rgb(255, 200, 200)', 'rgb(200, 0, 0)', 150, colortype='rgb')

In [ ]:
colors

In [ ]:
a = np.random.randint(low=0, high=150, size=150)

In [ ]:
a

In [ ]:
gentrification_rank_table['total_rank'].to_numpy()

In [ ]:
np.array(colors)[a]

In [ ]:
gentrification_rank_table.columns